In [1]:
import pandas as pd
import numpy as np

import plotly.graph_objects as go
import plotly.express as px
import plotly.io as pio

from scipy.stats import chisquare
from scipy.stats import mannwhitneyu

import re

import requests, sys

In [3]:
#!wget "https://kodomo.fbb.msu.ru/FBB/year_20/term4/human-genes.tsv" -O "human-genes.tsv"   #Таблица human-genes.tsv содержит информацию о генах человека (в том числе и о положении стартовых ATG)
data = pd.read_csv('human-genes.tsv', sep='\t')
server = "https://rest.ensembl.org"

In [4]:
GC_content_human_genome = 0.404     # ГЦ-состав в человеческом геноме
ps_co = 0.1                         # Значение псевдокаунта...
dict_apo_prob = {"A": (1-GC_content_human_genome)/2,
                 "T": (1-GC_content_human_genome)/2,
                 "G": GC_content_human_genome/2,
                 "C": GC_content_human_genome/2}
seed = 42

In [5]:
sample = data.sample(1000, random_state=seed)                        #Берём SRS (Simple random sampling) из таблицы генов.
sample_train, sample_test = sample[:500], sample[500:]    #Разделение на Train и Test. В Train возьмём 40 первых строк, в Test - 60 последних (поскольку изначально была взята SRS, случайность не нарушается)

In [6]:
#Train
with open("KozakTrain.fasta", "w") as out_file:
    chr_strand_start = list(map(lambda x: (x[1]["#chrom"][3:], 1 if x[1]["strand"] == "+" else -1, x[1]["thickStart"] if x[1]["strand"] == "+" else x[1]["thickEnd"]), sample_train.iterrows()))
    k = 0
    for chr, strand, start in chr_strand_start:           #Итерирование по кортежам вида (номер хромосомы, ориентация цепи, соответствующее ориентации начало ATG) 
        if k == 40:
            break
        if strand == 1:
            link = server + f"/sequence/region/human/{chr}:{start - 6}..{start + 6}:{strand}?expand_3prime=0;expand_5prime=0" 
        elif strand == -1:
            link = server + f"/sequence/region/human/{chr}:{start - 5}..{start + 7}:{strand}?expand_3prime=0;expand_5prime=0"   #Поправка на -1 ориентацию цепи
        r = requests.get(link, headers={ "Content-Type" : "text/x-fasta"})

        if not r.ok:
            r.raise_for_status()
            sys.exit()
        if r.text.split('\n')[1][7:10] == "ATG":
            print(r.text, file=out_file, end='')
            k += 1
        else:
            continue
        
#KozakTrain.fasta содержит все "обучающие" последовательности (материал обучения), по которым будет строится матрица PWM

#Test
with open("KozakTest.fasta", "w") as out_file:
    chr_strand_start = list(map(lambda x: (x[1]["#chrom"][3:], 1 if x[1]["strand"] == "+" else -1, x[1]["thickStart"] if x[1]["strand"] == "+" else x[1]["thickEnd"]), sample_test.iterrows()))
    k = 0
    for chr, strand, start in chr_strand_start:
        if k == 60:
            break
        if strand == 1:
            link = server + f"/sequence/region/human/{chr}:{start - 6}..{start + 6}:{strand}?expand_3prime=0;expand_5prime=0"
        elif strand == -1:
            link = server + f"/sequence/region/human/{chr}:{start - 5}..{start + 7}:{strand}?expand_3prime=0;expand_5prime=0"
        r = requests.get(link, headers={ "Content-Type" : "text/x-fasta"})

        if not r.ok:
            r.raise_for_status()
            sys.exit()

        if r.text.split('\n')[1][7:10] == "ATG":
            print(r.text, file=out_file, end='')
            k += 1
        else:
            continue

#KozakTest.fasta содержит последовательности, в которых ожидается встреча сигнала

#NegativeControl
sars_atg = pd.read_csv("sarsatg.tsv", sep="\t")              #Файл с разметкой ATG-триплетов. В нём указано, какие из ATG являются стартовыми (снабжёнными консенсусом Козак) 
sample = sars_atg.loc[(sars_atg.Pattern != "start_tr")&(sars_atg.Strand == "+"), :].sample(60, random_state=seed)          #Отбираю нестартовые ATG на + цепи (последнее для удобства) и беру случайную выборку в том же размере, что и KozakTest
starts = sample.Start.values - 1
with open("sequence.fasta", "r") as input_file:
    sequence = ''.join(map(lambda x: x.rstrip(), input_file.readlines()[1:]))
with open("KozakNegativeControl.fasta", "w") as out_file:
    for start in starts:
        print(sequence[start-7:start] + sequence[start:start+6], file=out_file)
        
#KozakNegativeControl.fasta содержит последовательности, включающие нестартовые ATG (без консенсуса Козак)

In [18]:
## Создание позиционной весовой матрицы...
with open("KozakTrain.fasta", "r") as input_file:    #Распаковываем train...
    text = input_file.readlines()
    train = list(map(lambda x: x.rstrip(), filter(lambda x: not x.startswith('>'), text)))
    train = np.array(list(map(lambda x: list(x), train)))
alignment_train = pd.DataFrame(train, columns=range(1, 14))      #DataFrame, в котором удобно считать встречаемость букв в каждом из столбцов выравнивания
alignment_train2 = pd.DataFrame(np.zeros((4, 13)), columns=range(1, 14), index=['A', 'T', 'G', 'C'])       #Пустой DataFrame, в который будем вставлять встречаемость букв в каждой из колонок
for i, col in alignment_train.iteritems():
    old = pd.DataFrame(alignment_train2.loc[:, i])
    new = pd.DataFrame(pd.Series(col).value_counts())
    alignment_train2.loc[:, i] = pd.merge(old, new, left_index=True, right_index=True, how="outer").iloc[:, 1].fillna(0)        #Сложный способ вставки встречаемости через merge...
    
PWM = alignment_train2.apply(lambda x: round(np.log(((x + ps_co)/(len(train) + 4*ps_co))/dict_apo_prob[x.name]), 3), axis=1)    #Построение PWM-матрицы по train-набору
PWM

C:\Temp\ipykernel_9540\2453306464.py:8: FutureWarning:

iteritems is deprecated and will be removed in a future version. Use .items instead.

C:\Temp\ipykernel_9540\2453306464.py:11: DeprecationWarning:

In a future version, `df.iloc[:, i] = newvals` will attempt to set the values inplace instead of always setting a new array. To retain the old behavior, use either `df[df.columns[i]] = newvals` or, if columns are non-unique, `df.isetitem(i, newvals)`

C:\Temp\ipykernel_9540\2453306464.py:11: DeprecationWarning:

In a future version, `df.iloc[:, i] = newvals` will attempt to set the values inplace instead of always setting a new array. To retain the old behavior, use either `df[df.columns[i]] = newvals` or, if columns are non-unique, `df.isetitem(i, newvals)`

C:\Temp\ipykernel_9540\2453306464.py:11: DeprecationWarning:

In a future version, `df.iloc[:, i] = newvals` will attempt to set the values inplace instead of always setting a new array. To retain the old behavior, use either `df[

1      2      3      4      5      6      7      8      9      10  \
A -0.680 -0.081 -0.176 -0.396  0.291  0.158 -0.680  1.203 -4.791 -4.791   
T  0.005 -0.280 -0.396 -0.859 -0.859 -0.528 -1.077 -4.791  1.203 -4.791   
G  0.308  0.547  0.109  0.308  0.547 -0.291  0.394 -4.402 -4.402  1.592   
C  0.308 -0.291  0.473  0.679 -0.470  0.473  0.797 -4.402 -4.402 -4.402   

      11     12     13  
A -0.396 -0.176 -0.680  
T  0.005 -0.280 -0.176  
G  0.308 -0.007  0.473  
C  0.109  0.473  0.308

In [8]:
#Подсчёт scores по PWM
with open("KozakTest.fasta", "r") as input_file:
    text = input_file.readlines()
    test = list(map(lambda x: x.rstrip(), filter(lambda x: not x.startswith('>'), text)))
    test = np.array(list(map(lambda x: list(x), test)))

positive = np.array(list(map(lambda x: sum(PWM.loc[i, j] for j, i in enumerate(x, 1)), test)))   #Подсчёт scores положительного контроля (test)
    
with open("KozakNegativeControl.fasta", "r") as input_file:
    text = input_file.readlines()
    neg = list(map(lambda x: x.rstrip(), filter(lambda x: not x.startswith('>'), text)))
    neg = np.array(list(map(lambda x: list(x), neg)))
    
negative = np.array(list(map(lambda x: sum(PWM.loc[i, j] for j, i in enumerate(x, 1)), neg)))      #Подсчёт scores отрицательного контроля (нестартовые ATG Sars Cov2)

train_sum = np.array(list(map(lambda x: sum(PWM.loc[i, j] for j, i in enumerate(x, 1)), train)))    #Подсчёт scores train

In [26]:
#Гистограмма scores, построенная в Plotly с использованием stack. 
fig = go.Figure()
fig.add_trace(go.Histogram(x=train_sum, name="Тренировочная выборка", opacity=0.6))
fig.add_trace(go.Histogram(x=positive, name="Тестовая выборка", opacity=0.6))
fig.add_trace(go.Histogram(x=negative, name="Негативный контроль", opacity=0.6))

# Stack histograms
fig.update_layout(barmode='overlay', width=800, height=600)
fig.show()
fig.write_html('Hist.html')

#Выберем порог score в 4 (Или в 4.1, или в 4.2, но, кажется, лучше в 4 :))

In [16]:
#Построим ради интереса boxplots (ящики с усами)
fig = go.Figure()
fig.add_trace(go.Box(y=train_sum, name="Train"))
fig.add_trace(go.Box(y=positive, name="Positive Control"))
fig.add_trace(go.Box(y=negative, name="Negative Control"))

fig.update_layout(
    width = 800, height=800,
    showlegend=False,
    margin = dict(l = 20, t = 20, r = 20, b = 20),
    font=dict(
        family="Futura",
        size=20
    )
)

fig.show()

# fig.show("notebook")

# fig.write_html('Boxplot.html')

#Очередное подтверждение тому, что имеется явное статистическое различие между Negative Control и Positive Control

In [17]:
#Таблица с определением количества последовательностей, попавших в выбранный порог
tresh = 4
final_table = pd.DataFrame(columns=["Train", "Test", "Negative Control"], index = ["сигнал(+)", "сигнал(-)"])
final_table.iloc[0, 0] = sum(train_sum > tresh) 
final_table.iloc[0, 1] = sum(positive > tresh) 
final_table.iloc[0, 2] = sum(negative > tresh) 
final_table.iloc[1, 0] = sum(train_sum <= tresh) 
final_table.iloc[1, 1] = sum(positive <= tresh) 
final_table.iloc[1, 2] = sum(negative <= tresh) 

final_table

Train Test Negative Control
сигнал(+)    29   47               16
сигнал(-)    11   13               44

In [13]:
#Строим матрицу IC
def func(x):
    if x != 0:
        return round((x/len(train))*np.log2(x/(len(train)*dict_apo_prob[line[0]])), 3)
    else:
        return 0

IC = pd.DataFrame(np.zeros((4, 13)), columns=range(1, 14), index=['A', 'T', 'G', 'C'])     
for line in alignment_train2.iterrows():
    l = line
    IC.loc[line[0], :] = np.array(list(map(func, line[1])))

    IC.reindex(index=['A', 'T', 'G', 'C', 'IC(j)'])
IC.loc["IC(j)", :] = IC.sum(axis=0)

IC

1      2      3      4      5      6      7      8      9      10  \
A     -0.149 -0.032 -0.063 -0.115  0.170  0.081 -0.149  1.747  0.000  0.000   
T      0.003 -0.091 -0.115 -0.157 -0.157 -0.134 -0.158  0.000  1.747  0.000   
G      0.122  0.278  0.035  0.122  0.278 -0.064  0.171  0.000  0.000  2.308   
C      0.122 -0.064  0.223  0.394 -0.087  0.223  0.520  0.000  0.000  0.000   
IC(j)  0.098  0.091  0.080  0.244  0.204  0.106  0.384  1.747  1.747  2.308   

          11     12     13  
A     -0.115 -0.063 -0.149  
T      0.003 -0.091 -0.063  
G      0.122 -0.003  0.223  
C      0.035  0.223  0.122  
IC(j)  0.045  0.066  0.133

In [27]:
#Задание№4
with open("E_coli_DSM_30083_complete genome.fasta", "r") as input_file:
    text = input_file.readlines()[1:]
    seq = ''.join(map(lambda x: x.rstrip(), text))

gc_cont = float(f"{((seq.count('C') + seq.count('G'))/len(seq)):0.3f}")
print(f'GC-content: {gc_cont}')

# gc_cont = 0.506     #GC-content выбранного штамма
pr_G = pr_C = gc_cont / 2
pr_A = pr_T = (1 - gc_cont) / 2
number_GAATTC = len(re.findall(r"GAATTC", seq))   #Использую re, хотя это не очень нужно...

from collections import Counter

def count_k_mers(seq, k):
    counts = Counter()
    
    num_kmers = len(seq) - k + 1
    
    for i in range(num_kmers):
        kmer = seq[i:i+k]
        counts[kmer] +=1
    return counts

counts = count_k_mers(seq, 6)
number_GAATTC = counts['GAATTC']       #Другой способ посчитать количество GAATTC-сайтов (и всех остальных 6-меров...)

print(f'Реальное количество 6-меров GAATTC: {number_GAATTC}')

exp_GAATTC = round((pr_G * pr_A * pr_A * pr_T * pr_T * pr_C) * len(seq))     #Ожидаемое число GAATTC сайтов с учётом GC-состава штамма

print(f'Ожидаемое количество 6-меров GAATTC: {exp_GAATTC}')

#Получается, что ожидаемое число GAATTC сайтов больше :)

print(f'Разность между ожидаемым и наблюдаемым количеством GAATTC сайтов в геноме выбранного штамма: {exp_GAATTC - number_GAATTC}')
p_value = chisquare([counts['GAATTC'], exp_GAATTC], ddof=0)[1]
print(f'p-value: {p_value}')
if p_value < 0.05:
      print('Разница между ожидаемым и наблюдаемым значениями всречаемости GAATTC статистически значима')
else:
      print('Разница между ожидаемым и наблюдаемым значениями всречаемости GAATTC статистически не значима')


GC-content: 0.507
Реальное количество 6-меров GAATTC: 694
Ожидаемое количество 6-меров GAATTC: 1163
Разность между ожидаемым и наблюдаемым количеством GAATTC сайтов в геноме выбранного штамма: 469
p-value: 1.3821855230087635e-27
Разница между ожидаемым и наблюдаемым значениями всречаемости GAATTC статистически значима
